## Ouvrir le fichier txt et convertir les positions des pixels en coordonnées

In [22]:
import math
import re
import json

def meters_to_longitude(distance_in_meters, latitude):
    degrees_longitude = distance_in_meters / (111000.0 * math.cos(math.radians(latitude)))
    return degrees_longitude

def pixels_to_coordinates(pixel, top_left_lat, top_left_lon, resolution_lat):
    x, y = pixel
    latitude = top_left_lat - (y * resolution_lat)
    degrees_longitude = (x * 10) / (111000.0 * math.cos(math.radians(latitude)))
    longitude = top_left_lon + degrees_longitude
    return latitude, longitude

# Coordonnées du coin supérieur gauche
top_left_latitude = 11.37
top_left_longitude = -3.89

# Résolution spatiale
resolution_lat = 1 / 111000

# Créer une liste pour stocker les nouvelles données avec les coordonnées géographiques
nouvelles_donnees = []

# ouvrir le fichier texte
fichier_texte = "contained_segments_50.txt"
with open(fichier_texte, 'r') as fichier:
    # Parcourir le fichier
    for ligne in fichier:
        # Extraire les positions des pixels
        match_pixels = re.search(r'Pixels: (\[\[.*\]\])', ligne)
        
        # Si une correspondance est trouvée, remplacer les positions par les coordonnées géographiques
        if match_pixels:
            positions_pixels = eval(match_pixels.group(1)) # converti la chaine de caractère en liste python
            
            # Convertir les positions en coordonnées géographiques
            coordonnees_geographiques = [pixels_to_coordinates(pixel, top_left_latitude, top_left_longitude, resolution_lat) for pixel in positions_pixels]
            
            # Remplacer les positions par les coordonnées géographiques dans la ligne
            # nouvelle_ligne = re.sub(r'Pixels: (\[\[.*\]\])', f'Coordinates: {coordonnees_geographiques}', ligne)
            nouvelle_ligne = re.sub(r'Pixels: (\[\[.*\]\])', f'Coordinates: {json.dumps(coordonnees_geographiques)}', ligne)
            
            # Ajouter la nouvelle ligne à la liste
            nouvelles_donnees.append(nouvelle_ligne.rstrip()) # supprimer les \n a la fin
        else:
            # Si aucune correspondance n'est trouvée, ajouter la ligne telle quelle à la liste
            nouvelles_donnees.append(ligne)

# Afficher les nouvelles données
for ligne in nouvelles_donnees:
    print(ligne.strip())


Segment ID: 367854, Polygon ID: 0.0, Class ID: 3.0, Coordinates: [[11.343684684684684, -3.7847915981978093], [11.343675675675675, -3.784791601516472], [11.343666666666666, -3.7847916048351316], [11.343657657657657, -3.7847916081537885], [11.343684684684684, -3.784699713130733], [11.343675675675675, -3.784699716452294], [11.343666666666666, -3.7846997197738523], [11.343657657657657, -3.784699723095408], [11.343684684684684, -3.784607828063657], [11.343675675675675, -3.7846078313881164], [11.343666666666666, -3.7846078347125727], [11.343657657657657, -3.7846078380370267], [11.343684684684684, -3.7845159429965807], [11.343675675675675, -3.7845159463239386], [11.343666666666666, -3.7845159496512935], [11.343657657657657, -3.7845159529786456]]
Segment ID: 367855, Polygon ID: 0.0, Class ID: 3.0, Coordinates: [[11.343648648648648, -3.7847916114724427], [11.343639639639639, -3.7847916147910943], [11.34363063063063, -3.7847916181097427], [11.34362162162162, -3.7847916214283885], [11.34364864864

In [23]:
nouvelles_donnees

['Segment ID: 367854, Polygon ID: 0.0, Class ID: 3.0, Coordinates: [[11.343684684684684, -3.7847915981978093], [11.343675675675675, -3.784791601516472], [11.343666666666666, -3.7847916048351316], [11.343657657657657, -3.7847916081537885], [11.343684684684684, -3.784699713130733], [11.343675675675675, -3.784699716452294], [11.343666666666666, -3.7846997197738523], [11.343657657657657, -3.784699723095408], [11.343684684684684, -3.784607828063657], [11.343675675675675, -3.7846078313881164], [11.343666666666666, -3.7846078347125727], [11.343657657657657, -3.7846078380370267], [11.343684684684684, -3.7845159429965807], [11.343675675675675, -3.7845159463239386], [11.343666666666666, -3.7845159496512935], [11.343657657657657, -3.7845159529786456]]',
 'Segment ID: 367855, Polygon ID: 0.0, Class ID: 3.0, Coordinates: [[11.343648648648648, -3.7847916114724427], [11.343639639639639, -3.7847916147910943], [11.34363063063063, -3.7847916181097427], [11.34362162162162, -3.7847916214283885], [11.34364

## Créer le fichier JSON

In [24]:
import json
import re

# Convertir les données en un format JSON
donnees_json = []
for ligne in nouvelles_donnees:
    # Extraire les ID du segment, du polygone et de la classe du texte
    segment_id = int(re.search(r'Segment ID: (\d+)', ligne).group(1))
    polygon_id = float(re.search(r'Polygon ID: ([\d.]+)', ligne).group(1))
    class_id = float(re.search(r'Class ID: ([\d.]+)', ligne).group(1))
    coordinates_text = re.search(r'Coordinates: (\[.*\])', ligne).group(1)
    
    # Convertir les coordonnées du texte en une liste Python
    coordinates_list = eval(coordinates_text)
    
    # Créer un dictionnaire avec les données nécessaires
    donnee_dict = {
        "Segment ID": segment_id,
        "Polygon ID": polygon_id,
        "Class ID": class_id,
        "Coordinates": coordinates_list
    }
    
    # Ajouter le dictionnaire à la liste des données JSON
    donnees_json.append(donnee_dict)

# Enregistrer les données JSON dans un fichier
with open('donnees.json', 'w') as fichier_json:
    json.dump(donnees_json, fichier_json, indent=2)
